### RAG Pipeline - Data Ingestion to Vector DB Pipeline

In [1]:
import os
from langchain_community.document_loaders import PyPDFLoader, PyMuPDFLoader
from langchain.text_splitter import RecursiveCharacterTextSplitter
from pathlib import Path

In [2]:
#### Read all the pdf(s) insdie the directory
def process_all_pdfs(pdf_directory):
    """Process all PDF files in a directory"""
    all_documents=[]
    pdf_dir=Path(pdf_directory)

    # Find all PDF files recursively
    pdf_files=list(pdf_dir.glob("**/*.pdf"))
    print(f'Found {len(pdf_files)} PDF files to process')
    for pdf_file in pdf_files:
        print(f'\nProcessing: {pdf_file.name}')
        try:
            loader=PyPDFLoader(str(pdf_file))
            documents=loader.load()

            # Add source information to metadata
            for doc in documents:
                doc.metadata['source_file']=pdf_file.name
                doc.metadata['file_type']='pdf'
            all_documents.extend(documents)
            print(f'Loaded {len(documents)} pages')
        except Exception as e:
            print(f'Error : {e}')

    print(f'\nTotal documents loaded: {len(all_documents)}')
    return all_documents

## process all PDF(s) in the data directory
all_pdf_documents=process_all_pdfs('../data/pdf')


Found 2 PDF files to process

Processing: LawsOfSalah.pdf
Loaded 326 pages

Processing: SummariesOfQuranicSuras.pdf
Loaded 302 pages

Total documents loaded: 628


In [10]:
### Text Splitting get in chunks

def split_document(documents,chunk_size=1000,chunk_overlap=200):
    """Split documents into smaller chunks for better RAG"""
    text_splitter=RecursiveCharacterTextSplitter(
        chunk_size=chunk_size,
        chunk_overlap=chunk_overlap,
        length_function=len,
        separators=["\n\n","\n"," ",""]
    )
    split_docs=text_splitter.split_documents(documents)
    print(f'Split {len(documents)} documents into {len(split_docs)} chunks')

    # show example of chunk
    if split_docs:
        print(f'\nExample chunk:')
        print(f'Content : {split_docs[0].page_content[:200]}...')
        print(f'Metadata: {split_docs[0].metadata}')

    return split_docs

In [11]:
chunks=split_document(all_pdf_documents)
chunks

Split 628 documents into 1415 chunks

Example chunk:
Content : /uni0645/uniFE8E/uniFB91/uniFEA3/uni064E/uni0627 /uniFBAF/uniFB90 /uni0632/uniFE8E /uni064E /uni06460645.init ) /uniFBFD/uni0650/uniFED4/uni064E/uniFEE8/uni064E/uniFEA3 (  
Namāz kay A /uni1E25 kām (/...
Metadata: {'producer': 'e-PDF Converter and Creator (http://www.e-pdfconverter.com)', 'creator': 'e-PDF Converter and Creator v2.1 - Build: Nov  1 2005', 'creationdate': '2010-10-21T20:25:24+00:00', 'author': 'Ameer-e-Ahle Sunnat', 'keywords': 'Method of  Wudu,Wudu and Science,Method of Ghusl,Blessings of Azan,Method of Salah,Traveller’s Ialah,Method of Missed Salah,Method of Funeral Salah,Blessings of Jumu’ah,Method of Eid Salah,40 Madani Wills,Method of Salah,Traveller’s Ialah,Method of Missed Salah,Method of Funeral Salah,Blessings of Jumu’ah,Method of Eid Salah,Method of Fatihah,namaz kay ahkam,laws of salah,نماز کے احکام', 'moddate': '2015-12-15T11:30:05+05:00', 'title': 'Laws of Salah - English', 'source': '..\\data\\

[Document(metadata={'producer': 'e-PDF Converter and Creator (http://www.e-pdfconverter.com)', 'creator': 'e-PDF Converter and Creator v2.1 - Build: Nov  1 2005', 'creationdate': '2010-10-21T20:25:24+00:00', 'author': 'Ameer-e-Ahle Sunnat', 'keywords': 'Method of  Wudu,Wudu and Science,Method of Ghusl,Blessings of Azan,Method of Salah,Traveller’s Ialah,Method of Missed Salah,Method of Funeral Salah,Blessings of Jumu’ah,Method of Eid Salah,40 Madani Wills,Method of Salah,Traveller’s Ialah,Method of Missed Salah,Method of Funeral Salah,Blessings of Jumu’ah,Method of Eid Salah,Method of Fatihah,namaz kay ahkam,laws of salah,نماز کے احکام', 'moddate': '2015-12-15T11:30:05+05:00', 'title': 'Laws of Salah - English', 'source': '..\\data\\pdf\\LawsOfSalah.pdf', 'total_pages': 326, 'page': 1, 'page_label': '2', 'source_file': 'LawsOfSalah.pdf', 'file_type': 'pdf'}, page_content='/uni0645/uniFE8E/uniFB91/uniFEA3/uni064E/uni0627 /uniFBAF/uniFB90 /uni0632/uniFE8E /uni064E /uni06460645.init ) /uni

### Embedding and VectorStoreDB

In [12]:
import numpy as np
from sentence_transformers import SentenceTransformer
import chromadb
from chromadb.config import Settings
import uuid
from typing import List, Dict, Any, Tuple
from sklearn.metrics.pairwise import cosine_similarity

In [13]:
class EmbeddingManager:
    """Handles document embedding generation using SentenceTransformer"""
    def __init__(self, model_name:str="all-MiniLM-L6-v2"):
        """
        Initialize the embedding manager

        Args:
            model_name: HuggingFace model name for sentence embeddings
        """
        self.model_name=model_name
        self.model=None
        self._load_model()
    
    def _load_model(self):
        """Load the sentenceTransformer model"""
        try:
            print(f'Loading embedding model: {self.model_name}')
            self.model=SentenceTransformer(self.model_name)
            print(f'Model loaded successfully. Embedding dimension: {self.model.get_sentence_embedding_dimension()}')
        except Exception as e:
            print(f'Error loading model {self.model_name}: {e}')
            raise

    def generate_embedding(self, texts:List[str]) -> np.ndarray:
        """
        Generate embedding for a list of texts.

        Args:
            text: List of text string to embed
        
        Returns:
            numpy array of embedding with shape(len(text), embedding_dim)
        """
        if not self.model:
            raise ValueError('Model not loaded')
        
        print(f'Generating embeddings for {len(texts)} texts ...')
        embeddings=self.model.encode(texts, show_progress_bar=True)
        print(f'Generated embedding with shape: {embeddings.shape}')
        return embeddings
        
    def get_embedding_dimension(self)->int:
        """Get the embedding dimension of the model"""
        if not self.model:
            raise ValueError('Model Not found')
        return self.model.get_sentence_embedding_dimension()



In [14]:
## Initialize rhe embeddingManager
embedding_manager=EmbeddingManager()
embedding_manager

Loading embedding model: all-MiniLM-L6-v2


c:\Users\sayubi\Documents\RAG_knowledge\.venv\Lib\site-packages\huggingface_hub\file_download.py:143: UserWarning: `huggingface_hub` cache-system uses symlinks by default to efficiently store duplicated files but your machine does not support them in C:\Users\sayubi\.cache\huggingface\hub\models--sentence-transformers--all-MiniLM-L6-v2. Caching files will still work but in a degraded version that might require more space on your disk. This warning can be disabled by setting the `HF_HUB_DISABLE_SYMLINKS_WARNING` environment variable. For more details, see https://huggingface.co/docs/huggingface_hub/how-to-cache#limitations.
To support symlinks on Windows, you either need to activate Developer Mode or to run Python as an administrator. In order to activate developer mode, see this article: https://docs.microsoft.com/en-us/windows/apps/get-started/enable-your-device-for-development
  warnings.warn(message)
Xet Storage is enabled for this repo, but the 'hf_xet' package is not installed. Fa

Model loaded successfully. Embedding dimension: 384


## VectorStore

In [15]:
class VectorStore:
    """Manages document embedding in a Chromadb vector store"""
    def __init__(self, collection_name: str="pdf_documents", persist_directory:str="../data/vector_store"):
        """
        Initialize the vector store
        
        Args:
            collection_name: Name of the ChromaDB collection
            persist_directory: Directory to presist the vector store
        """
        self.collection_name=collection_name
        self.persist_directory=persist_directory
        self.client=None
        self.collection=None
        self._initialize_store()

    def _initialize_store(self):
        """Initialize ChromaDB client and collection"""
        try:
            # Create persistent ChromaDB client
            os.makedirs(self.persist_directory,exist_ok=True)
            self.client=chromadb.PersistentClient(path=self.persist_directory)

            # Get or create collection
            self.collection=self.client.get_or_create_collection(
                name=self.collection_name,
                metadata={"description":"PDF document embedding for RAG"}
            )
            print(f'Vector store initialized, Collection: {self.collection_name}')
            print(f'Existing docuemnt in collection: {self.collection.count()}')

        except Exception as e:
            print(f'Error initializing vector store: {e}')
            raise
    
    def add_documents(self, documents: List[Any], embeddings: np.ndarray):
        """
        Add documents and their embeddings to the vector store

        Args:
            documents: List of Langchain documents
            embeddings: Corresponding embedding for the documents
        """
        if len(documents) != len(embeddings):
            raise ValueError('Number of documents must match number of embeddings')
        
        print(f'Adding {len(documents)} documents to vector store ...')

        # Prepare data for ChromaDB
        ids=[]
        metadatas=[]
        documents_text=[]
        embeddings_list= []

        for i, (doc, embedding) in enumerate(zip(documents,embeddings)):
            # Generate unique IDs
            doc_id=f'doc_{uuid.uuid4().hex[:8]}_{i}'
            ids.append(doc_id)

            # Prepare metadata
            metadata= dict(doc.metadata)
            metadata['doc_index']=i
            metadata['content_length']=len(doc.page_content)
            metadatas.append(metadata)

            # Document content
            documents_text.append(doc.page_content)

            # Embedding
            embeddings_list.append(embedding.tolist())

        # Add to collection
        try:
            self.collection.add(
                ids=ids,
                embeddings=embeddings_list,
                metadatas=metadatas,
                documents=documents_text
            )
            print(f'Successfully added {len(documents)} documents to vector store')
            print(f'Total documents in collection: {self.collection.count()}')
        except Exception as e:
            print(f'Error adding documents to vector store: {e}')
            raise



In [21]:
vector_store=VectorStore()
vector_store

Vector store initialized, Collection: pdf_documents
Existing docuemnt in collection: 0


In [17]:
chunks

[Document(metadata={'producer': 'e-PDF Converter and Creator (http://www.e-pdfconverter.com)', 'creator': 'e-PDF Converter and Creator v2.1 - Build: Nov  1 2005', 'creationdate': '2010-10-21T20:25:24+00:00', 'author': 'Ameer-e-Ahle Sunnat', 'keywords': 'Method of  Wudu,Wudu and Science,Method of Ghusl,Blessings of Azan,Method of Salah,Traveller’s Ialah,Method of Missed Salah,Method of Funeral Salah,Blessings of Jumu’ah,Method of Eid Salah,40 Madani Wills,Method of Salah,Traveller’s Ialah,Method of Missed Salah,Method of Funeral Salah,Blessings of Jumu’ah,Method of Eid Salah,Method of Fatihah,namaz kay ahkam,laws of salah,نماز کے احکام', 'moddate': '2015-12-15T11:30:05+05:00', 'title': 'Laws of Salah - English', 'source': '..\\data\\pdf\\LawsOfSalah.pdf', 'total_pages': 326, 'page': 1, 'page_label': '2', 'source_file': 'LawsOfSalah.pdf', 'file_type': 'pdf'}, page_content='/uni0645/uniFE8E/uniFB91/uniFEA3/uni064E/uni0627 /uniFBAF/uniFB90 /uni0632/uniFE8E /uni064E /uni06460645.init ) /uni

In [20]:
### Convert text to embeddings 

texts=[doc.page_content for doc in chunks]
texts

['/uni0645/uniFE8E/uniFB91/uniFEA3/uni064E/uni0627 /uniFBAF/uniFB90 /uni0632/uniFE8E /uni064E /uni06460645.init ) /uniFBFD/uni0650/uniFED4/uni064E/uniFEE8/uni064E/uniFEA3 (  \nNamāz kay A /uni1E25 kām (/uni1E24anafī) \n \nSALAH  \n \n \nShaykh-e-Tariqat, Ameer-e-Ahl-e-Sunnat, \nF\nounder of Dawat-e-Islami, Allamah Maulana Abu Bilal \nMuhammad Ilyas Attar \n \n \n \n \n/bullet.015 \nT\nranslated into English by \nMajlis-e-Tarajim (Dawat-e-Islami) \nQadiri Razavi دَا afii57416.initafii57433.zz03 \nL A W S  O F \nwww.dawateislami.net',
 'Laws of Salah (Hanafi) \nA\nn English translation of ‘Namaz kay Ahkam (Hanafi)’ \n/rhombus3 \nA LL R IGHTS R ESERVED  \nCopyright © 2015 Maktaba-tul-Madinah \n \nNo part of this publication may be reproduced, or transmitted, in any form or \nby any means, electronic, mechanical, photocopying, recording or otherwise, \nwithout the prior written permission of Maktaba-tul-Madinah. \n \n \nEdition:    First \n2nd  Publication:  Rabi’-us-Sani, 1436 AH – (Febru

In [22]:
## generate the embeddings from text

embeddings=embedding_manager.generate_embedding(texts)

## Store in the vector Database
vector_store.add_documents(chunks, embeddings)

Generating embeddings for 1415 texts ...


Batches: 100%|██████████| 45/45 [00:59<00:00,  1.31s/it]


Generated embedding with shape: (1415, 384)
Adding 1415 documents to vector store ...
Successfully added 1415 documents to vector store
Total documents in collection: 1415


## Retriever Pipeline From VectorStore

In [23]:
class RAGRetriever:
    """Handles query-based retrieval from the vector store"""
    def __init__(self, vector_store:VectorStore, embedding_manager:EmbeddingManager):
        """
        Initialize the retriever

        Args:
            vector_store: Vector store containing document embeddings
            embedding_manager: Manager for generating query embeddings
        """
        self.vector_store= vector_store
        self.embedding_manager=embedding_manager

        def retrieve(self, query:str, top_k: int=5, score_threshold:float=0.0) -> List[Dict[str,Any]]:
            """
            Retrieve relevant documents for a query

            Args:
                query: The search query
                top_k: Number of top results to return
                score_threshold: Minimum similarity score threshold

            Returns: 
                List of dictionaries containing retrieved documents and metadata
            """
            print(f"Retrieving documents for query: '{query}'")
            print(f'Top K: {top_k}, score threshold: {score_threshold}')

            # Generate query embedding
            query_embedding=self.embedding_manager.generate_embeddings([query])[0]

            # Search in vector store
            try:
                results=self.vector_store.collection.query(
                    query_embeddings=[query_embedding.tolist()],
                    n_results=top_k
                )
                # Process results
                retrieved_docs=[]

                if results['documents'] and results['documents'][0]:
                    documents=results['documents'][0]
                    metadatas=results['metadata'][0]
                    distances=results['distances'][0]
                    ids=results['ids'][0]

                    for i, (doc_id,document, metadata, distance) in enumerate(zip(ids,documents, metadatas, distances)):
                        # Convert distance to similarity score (ChromaDB uses cosine distance)
                        similarity_score=1-distance
                        if similarity_score>= score_threshold:
                            retrieved_docs.append({
                                'id':doc_id,
                                'content':document,
                                'metadata':metadata,
                                'similarity_score':similarity_score,
                                'distance':distance,
                                'rank':i+1
                            })
                    print(f'Retrived {len(retrieved_docs)} documents (after filtering)')
                else:
                    print('No Document found')
                
                return retrieved_docs
            except Exception as e:
                print(f'Error during retrieval: {e}')
                return []

